In [ ]:
import pandas as pd
import numpy as np
import xgboost as xgb
import optuna

In [39]:
test_data = pd.read_csv('/Users/baconbaker/Documents/Studium/ANM/anm-project/data/test_data/esb.csv')
train_data = pd.read_csv('/Users/baconbaker/Documents/Studium/ANM/anm-project/data/train_data/esb.csv')

print(test_data.head())
print(train_data.head())

  service_name     start_time  avg_time  num  succee_num  succee_rate
0      osb_001  1606881600000    0.6214  361         361       1.0000
1      osb_001  1606881660000    0.5861  343         343       1.0000
2      osb_001  1606881720000    5.0125  126         122       0.9683
3      osb_001  1606881780000    9.3487   70          70       1.0000
4      osb_001  1606881840000    1.4756  375         375       1.0000
  serviceName      startTime  avg_time  num  succee_num  succee_rate
0     osb_001  1588521600000    0.5691  347         347          1.0
1     osb_001  1588521660000    0.5813  354         354          1.0
2     osb_001  1588521720000    0.5397  363         363          1.0
3     osb_001  1588521780000    0.6190  387         387          1.0
4     osb_001  1588521840000    0.4909  387         387          1.0


In [40]:
#Reformatting train data
train_data['start_time'] = train_data['startTime']

In [41]:
def get_onehot(df):
    df['start_time'] = pd.to_datetime(df['start_time'], unit='ms', origin='unix')
    df['start_hour'] = df["start_time"].dt.strftime("%H")
    df['start_minute'] = df["start_time"].dt.strftime("%M")
    return df

def split(df):
    df_x = df[['start_hour', 'start_minute']].astype('int32')
    df_y = df[['num', 'avg_time']]
    return df_x, df_y

In [42]:
train_data = get_onehot(train_data)
train_x, train_y = split(train_data)

test_data = get_onehot(test_data)
test_x, test_y = split(test_data)

In [75]:
def objective(trial):
    param = {
        'max_depth': trial.suggest_int('depth', 2, 20),
        'eta': trial.suggest_float('eta', .8, 2),
        'objective': 'reg:squaredlogerror'}

    param['eval_metric'] = 'rmsle'
    evallist = [(dtest, 'eval'), (dtrain, 'train')]

    num_round = trial.suggest_int('rounds', 10, 300)
    model = xgb.train(param, dtrain, num_round, evallist, evals_result=progress)
    return progress['eval']['rmsle'][-1]
    

In [76]:
study = optuna.create_study()
study.optimize(objective, n_trials=5000)

param = study.best_params  # E.g. {'x': 2.002108042}
print(param)

[I 2020-12-03 18:22:15,813] A new study created in memory with name: no-name-009f3c48-9640-45c4-8493-4a9f69d7e4be


[0]	eval-rmsle:0.28167	train-rmsle:0.02782
[1]	eval-rmsle:0.28579	train-rmsle:0.02234
[2]	eval-rmsle:0.28518	train-rmsle:0.01948
[3]	eval-rmsle:0.28540	train-rmsle:0.01826
[4]	eval-rmsle:0.28523	train-rmsle:0.01737
[5]	eval-rmsle:0.28527	train-rmsle:0.01683
[6]	eval-rmsle:0.28561	train-rmsle:0.01593
[7]	eval-rmsle:0.28552	train-rmsle:0.01531
[8]	eval-rmsle:0.28558	train-rmsle:0.01474
[9]	eval-rmsle:0.28552	train-rmsle:0.01426
[10]	eval-rmsle:0.28533	train-rmsle:0.01387
[11]	eval-rmsle:0.28522	train-rmsle:0.01344
[12]	eval-rmsle:0.28537	train-rmsle:0.01302
[13]	eval-rmsle:0.28536	train-rmsle:0.01284
[14]	eval-rmsle:0.28530	train-rmsle:0.01262
[15]	eval-rmsle:0.28546	train-rmsle:0.01229
[16]	eval-rmsle:0.28552	train-rmsle:0.01198
[17]	eval-rmsle:0.28541	train-rmsle:0.01173
[18]	eval-rmsle:0.28535	train-rmsle:0.01157
[19]	eval-rmsle:0.28533	train-rmsle:0.01148
[20]	eval-rmsle:0.28534	train-rmsle:0.01130
[21]	eval-rmsle:0.28536	train-rmsle:0.01111
[22]	eval-rmsle:0.28548	train-rmsle:0.0109

[I 2020-12-03 18:22:16,170] Trial 0 finished with value: 0.285775 and parameters: {'depth': 8, 'eta': 1.2957166662218937, 'rounds': 175}. Best is trial 0 with value: 0.285775.


[0]	eval-rmsle:0.27466	train-rmsle:0.05198
[1]	eval-rmsle:0.30297	train-rmsle:0.05398
[2]	eval-rmsle:0.27786	train-rmsle:0.04255
[3]	eval-rmsle:0.29719	train-rmsle:0.04180
[4]	eval-rmsle:0.28060	train-rmsle:0.03546
[5]	eval-rmsle:0.29262	train-rmsle:0.03371
[6]	eval-rmsle:0.28320	train-rmsle:0.02717
[7]	eval-rmsle:0.28784	train-rmsle:0.02357
[8]	eval-rmsle:0.28466	train-rmsle:0.01910
[9]	eval-rmsle:0.28570	train-rmsle:0.01630
[10]	eval-rmsle:0.28502	train-rmsle:0.01383
[11]	eval-rmsle:0.28578	train-rmsle:0.01204
[12]	eval-rmsle:0.28597	train-rmsle:0.01093
[13]	eval-rmsle:0.28584	train-rmsle:0.00959
[14]	eval-rmsle:0.28566	train-rmsle:0.00872
[15]	eval-rmsle:0.28573	train-rmsle:0.00796
[16]	eval-rmsle:0.28579	train-rmsle:0.00758
[17]	eval-rmsle:0.28585	train-rmsle:0.00694
[18]	eval-rmsle:0.28586	train-rmsle:0.00635
[19]	eval-rmsle:0.28596	train-rmsle:0.00604
[20]	eval-rmsle:0.28589	train-rmsle:0.00577
[21]	eval-rmsle:0.28592	train-rmsle:0.00536
[22]	eval-rmsle:0.28596	train-rmsle:0.0050

[185]	eval-rmsle:0.28592	train-rmsle:0.00144
[186]	eval-rmsle:0.28592	train-rmsle:0.00144
[187]	eval-rmsle:0.28592	train-rmsle:0.00144
[188]	eval-rmsle:0.28592	train-rmsle:0.00144
[189]	eval-rmsle:0.28592	train-rmsle:0.00144
[190]	eval-rmsle:0.28592	train-rmsle:0.00144
[191]	eval-rmsle:0.28592	train-rmsle:0.00144


...

[0]	eval-rmsle:0.27381	train-rmsle:0.05752
[1]	eval-rmsle:0.30841	train-rmsle:0.06793
[2]	eval-rmsle:0.27445	train-rmsle:0.05459
[3]	eval-rmsle:0.30656	train-rmsle:0.06364
[4]	eval-rmsle:0.27474	train-rmsle:0.05216
[5]	eval-rmsle:0.30484	train-rmsle:0.06013
[6]	eval-rmsle:0.27505	train-rmsle:0.05011
[7]	eval-rmsle:0.30333	train-rmsle:0.05718
[8]	eval-rmsle:0.27541	train-rmsle:0.04833
[9]	eval-rmsle:0.30206	train-rmsle:0.05467
[10]	eval-rmsle:0.27573	train-rmsle:0.04678
[11]	eval-rmsle:0.30097	train-rmsle:0.05249
[12]	eval-rmsle:0.27603	train-rmsle:0.04540
[13]	eval-rmsle:0.30003	train-rmsle:0.05058
[14]	eval-rmsle:0.27630	train-rmsle:0.04418
[15]	eval-rmsle:0.29921	train-rmsle:0.04890
[16]	eval-rmsle:0.27678	train-rmsle:0.04308
[17]	eval-rmsle:0.29824	train-rmsle:0.04739
[18]	eval-rmsle:0.27691	train-rmsle:0.04207
[19]	eval-rmsle:0.29826	train-rmsle:0.04603
[20]	eval-rmsle:0.27716	train-rmsle:0.04114
[21]	eval-rmsle:0.29714	train-rmsle:0.04480
[22]	eval-rmsle:0.27687	train-rmsle:0.0403

[I 2020-12-03 18:30:41,689] Trial 4998 finished with value: 0.276872 and parameters: {'depth': 2, 'eta': 1.9996559249773422, 'rounds': 23}. Best is trial 2602 with value: 0.276278.


[0]	eval-rmsle:0.27441	train-rmsle:0.05354
[1]	eval-rmsle:0.30470	train-rmsle:0.05751
[2]	eval-rmsle:0.27725	train-rmsle:0.04554
[3]	eval-rmsle:0.30003	train-rmsle:0.04737
[4]	eval-rmsle:0.27924	train-rmsle:0.03894
[5]	eval-rmsle:0.29493	train-rmsle:0.03852
[6]	eval-rmsle:0.28048	train-rmsle:0.03196
[7]	eval-rmsle:0.28949	train-rmsle:0.03083
[8]	eval-rmsle:0.28188	train-rmsle:0.02650
[9]	eval-rmsle:0.28933	train-rmsle:0.02503
[10]	eval-rmsle:0.28261	train-rmsle:0.02150
[11]	eval-rmsle:0.28866	train-rmsle:0.01987
[12]	eval-rmsle:0.28337	train-rmsle:0.01729
[13]	eval-rmsle:0.28766	train-rmsle:0.01604
[14]	eval-rmsle:0.28467	train-rmsle:0.01475
[15]	eval-rmsle:0.28669	train-rmsle:0.01359
[16]	eval-rmsle:0.28505	train-rmsle:0.01258
[17]	eval-rmsle:0.28613	train-rmsle:0.01156
[18]	eval-rmsle:0.28553	train-rmsle:0.01084
[19]	eval-rmsle:0.28595	train-rmsle:0.01013
[20]	eval-rmsle:0.28562	train-rmsle:0.00955
[21]	eval-rmsle:0.28581	train-rmsle:0.00914
[22]	eval-rmsle:0.28612	train-rmsle:0.0086

[I 2020-12-03 18:30:41,898] Trial 4999 finished with value: 0.285851 and parameters: {'depth': 9, 'eta': 1.9203148350602897, 'rounds': 37}. Best is trial 2602 with value: 0.276278.


{'depth': 2, 'eta': 1.9999870742844794, 'rounds': 15}


In [77]:
dtrain = xgb.DMatrix(train_x, label=train_y[['avg_time']])
dtest = xgb.DMatrix(test_x, label=test_y[['avg_time']])

param = {
    'max_depth': 2,
    'eta': 2,
    'objective': 'reg:squaredlogerror'}

param['eval_metric'] = 'rmsle'
evallist = [(dtest, 'eval'), (dtrain, 'train')]
progress = {}

num_round = 15
model = xgb.train(param, dtrain, num_round, evallist, evals_result=progress)
print(progress['eval']['rmsle'][-1])

[0]	eval-rmsle:0.27381	train-rmsle:0.05754
[1]	eval-rmsle:0.30844	train-rmsle:0.06798
[2]	eval-rmsle:0.27444	train-rmsle:0.05464
[3]	eval-rmsle:0.30660	train-rmsle:0.06372
[4]	eval-rmsle:0.27473	train-rmsle:0.05222
[5]	eval-rmsle:0.30489	train-rmsle:0.06024
[6]	eval-rmsle:0.27504	train-rmsle:0.05018
[7]	eval-rmsle:0.30339	train-rmsle:0.05731
[8]	eval-rmsle:0.27539	train-rmsle:0.04842
[9]	eval-rmsle:0.30213	train-rmsle:0.05481
[10]	eval-rmsle:0.27571	train-rmsle:0.04688
[11]	eval-rmsle:0.30105	train-rmsle:0.05264
[12]	eval-rmsle:0.27601	train-rmsle:0.04551
[13]	eval-rmsle:0.30011	train-rmsle:0.05075
[14]	eval-rmsle:0.27628	train-rmsle:0.04429
0.276278
